In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
f = open('/home/andrei/my-bucket/3D-FRONT/0b2bc0ab-adef-4db2-b681-84b8adf592ed.json')

In [3]:
path_to_3d_front_dataset_directory = '/home/andrei/my-bucket/3D-FRONT/'
path_to_model_info = '/home/andrei/my-bucket/3D-FUTURE-model-part1/model_info.json'
path_to_3d_future_dataset_directory = '/home/andrei/my-bucket/3D-FUTURE-model-part1'
from scene_synthesis.datasets.threed_front import ThreedFront
d = ThreedFront.from_dataset_directory(
        path_to_3d_front_dataset_directory,
        path_to_model_info,
        path_to_3d_future_dataset_directory,
        path_to_room_masks_dir=None,
        path_to_bounds=None,
        filter_fn=lambda s: s)

Loading dataset     0 /  681    1 /  681    2 /  681    3 /  681    4 /  681    5 /  681


In [4]:
len(d)

19

In [5]:
path_to_floor_plan_textures = '/home/andrei/my-bucket/3D-FRONT-texture'

In [6]:
for c in d.scenes:
    print(c.scene_id)

Library-4425
MasterBedroom-5863
SecondBedroom-7177
LivingDiningRoom-3474
LivingRoom-54780
Bedroom-54672
DiningRoom-54730
Bedroom-43072
Hallway-44736
LivingDiningRoom-44785
MasterBedroom-18030
DiningRoom-17932
LivingRoom-17888
SecondBedroom-17954
SecondBedroom-17992
MasterBedroom-282636
LivingRoom-282598
SecondBedroom-282617
Bedroom-7177


In [7]:
s = d.scenes[2]

In [8]:
s.scene_id

'SecondBedroom-7177'

In [9]:
s.scene_id

'SecondBedroom-7177'

In [10]:
b = s.bboxes[0]

In [11]:
for b in s.bboxes:
    print(b.model_jid)

bcb9884d-d032-40df-b2e1-c2bb467a02e8
73e85e57-b389-494b-81dc-5827c238cb1b
ff62d9c3-1813-406a-88c2-427eaaee4578
a32fbc3e-32e7-44a9-b947-306c42d3a34d


In [12]:
print(b.model_jid, b.label)
print(s.furniture_in_room, s.scene_id, s.json_path)

a32fbc3e-32e7-44a9-b947-306c42d3a34d pendant lamp
['king-size bed', 'drawer chest/corner cabinet', 'wardrobe', 'pendant lamp'] SecondBedroom-7177 00004f89-9aa5-43c2-ae3c-129586be8aaa


In [19]:
import numpy as np
import os
from simple_3dviz import Scene
from simple_3dviz.behaviours.keyboard import SnapshotOnKey
from simple_3dviz.behaviours.io import SaveFrames
from simple_3dviz.renderables.textured_mesh import TexturedMesh
from simple_3dviz.utils import render
from simple_3dviz.window import show

import trimesh
from PIL import Image
from scripts.utils import floor_plan_from_scene, export_scene

In [14]:
%matplotlib inline


In [15]:
from xvfbwrapper import Xvfb

In [16]:
# Start the virtual framebuffer
xvfb = Xvfb(width=1280, height=720)
xvfb.start()

In [22]:
behaviours = []
for b in s.bboxes:
    renderables = s.furniture_renderables(
        with_floor_plan_offset=True, with_texture=True
    )
    trimesh_meshes = []
    for furniture in s.bboxes:
        # Load the furniture and scale it as it is given in the dataset
        raw_mesh = TexturedMesh.from_file(furniture.raw_model_path)
        raw_mesh.scale(furniture.scale)

        # Create a trimesh object for the same mesh in order to save
        # everything as a single scene
        tr_mesh = trimesh.load(furniture.raw_model_path, force="mesh")
        tr_mesh.visual.material.image = Image.open(
            furniture.texture_image_path
        )
        tr_mesh.vertices *= furniture.scale
        theta = furniture.z_angle
        R = np.zeros((3, 3))
        R[0, 0] = np.cos(theta)
        R[0, 2] = -np.sin(theta)
        R[2, 0] = np.sin(theta)
        R[2, 2] = np.cos(theta)
        R[1, 1] = 1.
        tr_mesh.vertices[...] = \
            tr_mesh.vertices.dot(R) + furniture.position
        tr_mesh.vertices[...] = tr_mesh.vertices - s.centroid
        trimesh_meshes.append(tr_mesh)

    if True:
        # Get a floor plan
        floor_plan, tr_floor, _ = floor_plan_from_scene(
            s, path_to_floor_plan_textures, without_room_mask=True
        )
        renderables += floor_plan
        trimesh_meshes += tr_floor

    if True:
        # show(
        #     renderables,
        #     behaviours=behaviours+[SnapshotOnKey()],
        #     size=(512,512),
        #     camera_position=(-2.0,-2.0,-2.0),
        #     camera_target=(0,0,0),
        #     light=(-2.0,-2.0,-2.0),
        #     up_vector=(0,0,1),
        #     background=(1,1,1,1),
        # )
        path_to_image = "{}/{}_".format('./', s.uid)
        behaviours += [SaveFrames(path_to_image+"{:03d}.png", 1)]
        render(
            renderables,
            size=(512,512),
            camera_position=(2.0, 2.0, 2.0),
            camera_target=(0,0,0),
            up_vector=(0,0,1),
            background=(1,1,1,1),
            behaviours=behaviours,
            n_frames=2,
            )
    # Create a trimesh scene and export it
    path_to_objs = os.path.join(
        './',
        "train_{}".format(1)
    )
    if not os.path.exists(path_to_objs):
        os.mkdir(path_to_objs)
    export_scene(path_to_objs, trimesh_meshes)


In [5]:
import json

json.load(f)

{'uid': '0b2bc0ab-adef-4db2-b681-84b8adf592ed',
 'jobid': '',
 'design_version': 'v1587200737',
 'code_version': '0.10',
 'north_vector': [0, 1, 0],
 'furniture': [{'uid': '26000/model',
   'jid': 'e5f584d0-bb1e-4e0a-8c1f-79d315ec6f84',
   'aid': [],
   'title': 'curtain/curtain',
   'type': 'standard'},
  {'uid': '25984/model0',
   'jid': '844f3e62-b2f4-4704-affb-ac10d3593213',
   'aid': [],
   'title': 'curtain/curtain',
   'type': 'standard'},
  {'uid': '25970/model0',
   'jid': '025cdd95-87c1-44d3-a51c-e6fb0825df11',
   'aid': [],
   'title': 'curtain/curtain',
   'type': 'standard'},
  {'uid': '26005/model',
   'jid': 'b31cc2af-6549-4422-8f96-ec5cd8f0f92c',
   'aid': [],
   'title': 'table/table',
   'type': 'standard',
   'size': [1.9029600524902344, 0.6983429718017579, 0.7297470092773437],
   'sourceCategoryId': '5c76d84c-aa8c-4bb8-88fc-cbf8da81be71',
   'bbox': [1.9029600524902344, 0.6983429718017579, 0.7297470092773437],
   'valid': True},
  {'uid': '26009/model',
   'jid': 'd